<span style="font-size: 14pt">MIPT, Applied ML, Autumn 2018</span>

<span style="font-size: 16pt"> HW #4: Approximate RL homework

<span style="color:red; font-size: 14pt;"> Дедлайн 19.11.2018 23:59 </span>

<span style="color:blue; font-size: 12pt">Valentin Malykh </span>,
<span style="color:blue; font-size: 12pt; font-family: 'Verdana'">val@maly.hk</span>


**Оформление дз**: 
- Выполненное задание требуется отправлять через <a href='https://goo.gl/forms/XPSIbwp7wPxB4SsI3'>форму </a>

- Выполненное дз прикрепляйте в формате файла ``<фамилия>_<группа>_task<номер>.ipynb``, например: ``ivanov_594_task4.ipynb`` 

**Вопросы**:
- Вопросы присылайте в канал в телеграмме ``[Fall 2018]ML Seminars``

--------
- **PS1**: Будьте внимательны при заполнении формы, когда отправляете ДЗ 


<h1 align="center">Практическое задание (100%)</h1>
Описание находится по ссылке: https://gist.github.com/madrugado/1262c3077bf7d8ac8166e4350f0f67e2

In [15]:
import gym
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline

In [16]:
import time
import keras

from keras.models import Sequential
from keras.layers import Dense, Dropout
from keras.layers import Embedding
from keras import optimizers

In [17]:
env = gym.make("LunarLander-v2")

[2018-11-16 15:10:28,735] Making new env: LunarLander-v2


In [36]:
def Q(s, a, p):
    return model.predict(np.concatenate((s, np.eye(4)[a], p), axis=0).reshape(1, -1))[0][0]

In [37]:
def Q(s, a):
    return model.predict(np.concatenate((s, np.eye(4)[a]), axis=0).reshape(1, -1))[0][0]

def use_prob(episode):
    return 0.05*(1 - episode/num_episodes)

In [19]:
import h5py

In [57]:
# Загрузить модель, обученную на 10000 эпизодах
model = keras.models.load_model("imodel10ktr.mdh5")

In [79]:
# Загрузить модель, обученную на 50000 эпизодах - дает наилучшие результаты
model = keras.models.load_model("model50k.mdh5")

In [78]:
# Загрузить модель, обученную на 100000 эпизодах и учетом луны
model = keras.models.load_model("i512model100ktr.mdh5")

In [20]:
# Обучить новую модель

dimX = 8 + 4
num_episodes = 10000

model = Sequential()
model.add(Dense(512, activation='relu', input_dim=dimX))
model.add(Dense(1))
model.compile(loss='mse', optimizer=optimizers.adam(lr=0.001), metrics=['accuracy'])

dataX = np.zeros(shape=(1, dimX))
dataY = np.zeros(shape=(1, 1))

over_ind = 0

for episode in range(num_episodes):
    e_dataX = np.zeros(shape=(1, dimX))
    e_dataY = np.zeros(shape=(1, 1))
    
    s = env.reset()
    total_r = 0
    First = True
    
    while True:
        if episode % 100 == 0:
            env.render()
        
        if np.random.rand(1) < use_prob(episode):
            a=env.action_space.sample()
        else:
            a = np.argmax(np.array([Q(s, 0), Q(s, 1), Q(s, 2), Q(s, 3)]))

        string = np.concatenate((s, np.eye(4)[a]), axis=0)

        new_s, r, done, info = env.step(a)


        if First:
            e_dataX[0] = string
            e_dataY[0] = np.array([r])
            dataX[0] = string
            dataY[0] = np.array([r])
            First = False

        e_dataX = np.vstack((e_dataX, string))
        e_dataY = np.vstack((e_dataY, np.array([r])))

        total_r += r

        s = new_s
        
        if done:
#             if total_r >= 200:
#                 r = 1000
            n = len(e_dataY)
            for i in range(1, n):
                e_dataY[n - i - 1][0] = e_dataY[n - i - 1][0] + 0.98 * e_dataY[n - i][0]
            
            print("Episode №", episode, " last reward = ", r, ", total reward = ", total_r)

            if len(dataX) == 1:
                dataX = e_dataX
                dataY = e_dataY
            else:
                dataX = np.concatenate((dataX, e_dataX), axis=0)
                dataY = np.concatenate((dataY, e_dataY), axis=0)

            if len(dataX) > 60000:
                dataX = np.delete(dataX, range(over_ind, over_ind + len(e_dataX)), axis=0)
                dataY = np.delete(dataY, range(over_ind, over_ind + len(e_dataX)), axis=0)
                over_ind += len(e_dataX)
                if over_ind > 59800:
                    over_ind = 0

            if episode%10 == 0:
                model.fit(dataX, dataY, batch_size=32, epochs=2, verbose=0)
            break
env.close()

Episode № 0  last reward =  -100 , total reward =  -728.3917877913353
Episode № 1  last reward =  -100 , total reward =  -232.08456971455882
Episode № 2  last reward =  -100 , total reward =  -247.6081099849279
Episode № 3  last reward =  -100 , total reward =  -416.192534130503
Episode № 4  last reward =  -100 , total reward =  -389.9031199592027
Episode № 5  last reward =  -100 , total reward =  -384.58903254630775
Episode № 6  last reward =  -100 , total reward =  -295.361172064294
Episode № 7  last reward =  -100 , total reward =  -420.8900507342421
Episode № 8  last reward =  -100 , total reward =  -422.77535799343235
Episode № 9  last reward =  -100 , total reward =  -294.0790565549221
Episode № 10  last reward =  -100 , total reward =  -339.5548329370802
Episode № 11  last reward =  -100 , total reward =  -559.2779568995559
Episode № 12  last reward =  -100 , total reward =  -523.1653726103658
Episode № 13  last reward =  -100 , total reward =  -393.872740288826
Episode № 14  la

Episode № 116  last reward =  -100 , total reward =  -325.78003936561004
Episode № 117  last reward =  -100 , total reward =  -209.9264878817616
Episode № 118  last reward =  -100 , total reward =  -166.538274330757
Episode № 119  last reward =  -100 , total reward =  -164.65950610187224
Episode № 120  last reward =  -100 , total reward =  -175.03408321167043
Episode № 121  last reward =  -100 , total reward =  -172.3139912057246
Episode № 122  last reward =  -100 , total reward =  -178.6836127154371
Episode № 123  last reward =  -100 , total reward =  -154.94197049511425
Episode № 124  last reward =  -100 , total reward =  -225.44731537738255
Episode № 125  last reward =  -100 , total reward =  -205.66723105227263
Episode № 126  last reward =  -100 , total reward =  -157.9712930290357
Episode № 127  last reward =  -100 , total reward =  -170.69755865346806
Episode № 128  last reward =  -100 , total reward =  -139.44619214703266
Episode № 129  last reward =  -100 , total reward =  -186

Episode № 230  last reward =  -100 , total reward =  -193.29050147023975
Episode № 231  last reward =  -100 , total reward =  -158.99364095073594
Episode № 232  last reward =  -100 , total reward =  -138.008388031052
Episode № 233  last reward =  -100 , total reward =  -68.9811199842055
Episode № 234  last reward =  -100 , total reward =  -164.88559877275034
Episode № 235  last reward =  -100 , total reward =  -93.28187149840852
Episode № 236  last reward =  -100 , total reward =  -60.173364180076746
Episode № 237  last reward =  -100 , total reward =  -64.94180528450664
Episode № 238  last reward =  -100 , total reward =  -180.15539488638387
Episode № 239  last reward =  -100 , total reward =  -59.42124238165458
Episode № 240  last reward =  -100 , total reward =  -64.01473542317434
Episode № 241  last reward =  -100 , total reward =  -139.8444074617872
Episode № 242  last reward =  -100 , total reward =  -191.09649721901772
Episode № 243  last reward =  -100 , total reward =  -86.356

Episode № 344  last reward =  -100 , total reward =  -190.32243762273413
Episode № 345  last reward =  -100 , total reward =  -142.16062560225333
Episode № 346  last reward =  -100 , total reward =  -143.79894656278594
Episode № 347  last reward =  -100 , total reward =  -144.58340413608818
Episode № 348  last reward =  -100 , total reward =  -147.99467942555862
Episode № 349  last reward =  -100 , total reward =  -141.89539305974898
Episode № 350  last reward =  -100 , total reward =  -184.10535123806085
Episode № 351  last reward =  -100 , total reward =  -124.26720936947268
Episode № 352  last reward =  -100 , total reward =  -206.16076154396526
Episode № 353  last reward =  -100 , total reward =  -36.92545505869836
Episode № 354  last reward =  -100 , total reward =  -163.630662812708
Episode № 355  last reward =  -100 , total reward =  -208.7565807470047
Episode № 356  last reward =  -100 , total reward =  -147.74932872804067
Episode № 357  last reward =  -100 , total reward =  -1

Episode № 457  last reward =  -100 , total reward =  -138.99291269083832
Episode № 458  last reward =  -100 , total reward =  -152.83646373918367
Episode № 459  last reward =  -100 , total reward =  -150.02181020813464
Episode № 460  last reward =  -100 , total reward =  -147.115171854262
Episode № 461  last reward =  -100 , total reward =  -157.4744116868926
Episode № 462  last reward =  -100 , total reward =  -155.29693495592576
Episode № 463  last reward =  -100 , total reward =  -140.59405570679246
Episode № 464  last reward =  -100 , total reward =  -160.35524818429877
Episode № 465  last reward =  -100 , total reward =  -179.59297387498054
Episode № 466  last reward =  -100 , total reward =  -180.4837464047529
Episode № 467  last reward =  -100 , total reward =  -191.14056588790925
Episode № 468  last reward =  -100 , total reward =  -161.6610033900114
Episode № 469  last reward =  -100 , total reward =  -185.91288046428176
Episode № 470  last reward =  -100 , total reward =  -81

...

Episode № 99541  last reward =  1000 , total reward =  203.89092790301606
Episode № 99542  last reward =  -100 , total reward =  -19.341587189148527
Episode № 99543  last reward =  100 , total reward =  174.88309506884042
Episode № 99544  last reward =  -0.015592025385245734 , total reward =  129.56053510212
Episode № 99545  last reward =  1000 , total reward =  225.9663816805921
Episode № 99546  last reward =  1000 , total reward =  252.64722221881757
Episode № 99547  last reward =  1000 , total reward =  245.40296627419903
Episode № 99548  last reward =  1000 , total reward =  221.14019764107002
Episode № 99549  last reward =  -100 , total reward =  -85.71557622473435
Episode № 99550  last reward =  1000 , total reward =  218.1717879486203
Episode № 99551  last reward =  0.03571781850334446 , total reward =  24.64034933601298
Episode № 99552  last reward =  -100 , total reward =  -20.757225845317336
Episode № 99553  last reward =  100 , total reward =  81.0824554933123
Episode № 9955

Episode № 99652  last reward =  1000 , total reward =  259.53561172351556
Episode № 99653  last reward =  1000 , total reward =  248.41449939986418
Episode № 99654  last reward =  1000 , total reward =  253.8718713480909
Episode № 99655  last reward =  -100 , total reward =  -17.712521555316258
Episode № 99656  last reward =  1000 , total reward =  249.5794739649498
Episode № 99657  last reward =  100 , total reward =  199.9433559791671
Episode № 99658  last reward =  -100 , total reward =  -30.538758375683713
Episode № 99659  last reward =  1000 , total reward =  247.90488978415837
Episode № 99660  last reward =  -100 , total reward =  -63.61714917474512
Episode № 99661  last reward =  100 , total reward =  198.18602851701013
Episode № 99662  last reward =  1000 , total reward =  227.46239048382617
Episode № 99663  last reward =  1000 , total reward =  216.65736120214586
Episode № 99664  last reward =  1000 , total reward =  236.27547536585158
Episode № 99665  last reward =  100 , tot

Episode № 99763  last reward =  1000 , total reward =  236.0906625735429
Episode № 99764  last reward =  1000 , total reward =  222.71409068919104
Episode № 99765  last reward =  1000 , total reward =  231.08451672764153
Episode № 99766  last reward =  100 , total reward =  152.90760225069005
Episode № 99767  last reward =  100 , total reward =  190.25242375099268
Episode № 99768  last reward =  100 , total reward =  119.82610899273129
Episode № 99769  last reward =  1000 , total reward =  207.84412419814234
Episode № 99770  last reward =  1000 , total reward =  239.7320061230035
Episode № 99771  last reward =  1000 , total reward =  202.6675928903483
Episode № 99772  last reward =  100 , total reward =  194.46585087125953
Episode № 99773  last reward =  1000 , total reward =  208.77135835631896
Episode № 99774  last reward =  1000 , total reward =  214.4938306157726
Episode № 99775  last reward =  100 , total reward =  170.66457801747902
Episode № 99776  last reward =  100 , total rew

Episode № 99874  last reward =  1000 , total reward =  243.77947935196306
Episode № 99875  last reward =  1000 , total reward =  240.34014316067174
Episode № 99876  last reward =  1000 , total reward =  211.58209575329224
Episode № 99877  last reward =  1000 , total reward =  200.38089836088471
Episode № 99878  last reward =  1000 , total reward =  210.29546483111966
Episode № 99879  last reward =  1000 , total reward =  245.35005993016273
Episode № 99880  last reward =  1000 , total reward =  214.17654402293414
Episode № 99881  last reward =  -100 , total reward =  -54.21698235022224
Episode № 99882  last reward =  100 , total reward =  185.4347996646403
Episode № 99883  last reward =  1000 , total reward =  246.81522611340054
Episode № 99884  last reward =  100 , total reward =  140.11250554074266
Episode № 99885  last reward =  1000 , total reward =  209.74262036051198
Episode № 99886  last reward =  1000 , total reward =  233.3205663831441
Episode № 99887  last reward =  100 , tota

Episode № 99986  last reward =  1000 , total reward =  216.2822522409421
Episode № 99987  last reward =  -100 , total reward =  -140.0178572978588
Episode № 99988  last reward =  1000 , total reward =  206.3560686672871
Episode № 99989  last reward =  1000 , total reward =  242.25588166320054
Episode № 99990  last reward =  -100 , total reward =  -15.470047305662277
Episode № 99991  last reward =  1000 , total reward =  202.5055298427383
Episode № 99992  last reward =  1000 , total reward =  238.74631070789746
Episode № 99993  last reward =  1000 , total reward =  241.36154256728932
Episode № 99994  last reward =  1000 , total reward =  217.1862659253
Episode № 99995  last reward =  100 , total reward =  197.98637851184586
Episode № 99996  last reward =  -100 , total reward =  -9.900349231526732
Episode № 99997  last reward =  -100 , total reward =  -77.40862826003314
Episode № 99998  last reward =  -100 , total reward =  -69.80562024999978
Episode № 99999  last reward =  -100 , total 

In [38]:
def play_n_episodes(n, rend = False):
    wins_cnt = 0
    for episode in range(n):
        s = env.reset()
        total_r = 0
        while True:
#             env.render()
            a = np.argmax(np.array([Q(s, 0), Q(s, 1), Q(s, 2), Q(s, 3)]))
            new_s, r, done, info = env.step(a)
            total_r += r
            s = new_s
            if done:
                if total_r >= 200:
                    print("total reward - " + str(total_r) + ", WIN")
                    wins_cnt += 1
                else:
                    print("total reward - " + str(total_r) + ", LOSE")
                break
    print("Wins " + str(wins_cnt) + " of " + str(n) + " episodes.")
    env.close()

In [81]:
play_n_episodes(10)

total reward - 215.90487014632544, WIN
total reward - 228.99222923197436, WIN
total reward - 235.4016250849651, WIN
total reward - 221.47740988970259, WIN
total reward - 212.72065215700349, WIN
total reward - 218.18788523129857, WIN
total reward - 204.07505536510232, WIN
total reward - 216.23714528085668, WIN
total reward - 226.82981262472754, WIN
total reward - 262.94399702637804, WIN
Wins 10 of 10 episodes.
